In [1]:
import os
path = os.getcwd()
print(path)

In [2]:
import sys
import numpy as np
import pandas as pd
from math import ceil
from itertools import islice
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import normalize
from sklearn.neighbors import NearestNeighbors
from scipy.sparse import csr_matrix, dok_matrix
from tqdm import trange

In [3]:
file_dir = 'ml-1m'
file_path = os.path.join(path, file_dir,'ratings.dat')
print(file_path)

/Users/akshitgupta/Downloads/BPR-MF/ml-1m/ratings.dat


In [4]:
names = ['user_id', 'item_id', 'rating', 'timestamp']
df = pd.read_csv(file_path, sep = '::', names = names)
print('data dimension: \n', df.shape)
df.head()

<ipython-input-4-62dd7f865362>:2: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  df = pd.read_csv(file_path, sep = '::', names = names)


data dimension: 
 (1000209, 4)


user_id  item_id  rating  timestamp
0        1     1193       5  978300760
1        1      661       3  978302109
2        1      914       3  978301968
3        1     3408       4  978300275
4        1     2355       5  978824291

In [5]:
def create_matrix(data, users_col, items_col, ratings_col, threshold = None):
   
    if threshold is not None:
        data = data[data[ratings_col] >= threshold]
        data[ratings_col] = 1
    
    for col in (items_col, users_col, ratings_col):
        print(col)
        data[col] = data[col].astype('category')

    ratings = csr_matrix((data[ratings_col],
                          (data[users_col].cat.codes, data[items_col].cat.codes)))
    ratings.eliminate_zeros()
    return ratings, data

In [6]:
items_col = 'item_id'
users_col = 'user_id'
ratings_col = 'rating'
# rating threshold, ratings above 3 considered as 1, below considered 0
threshold = 3 
X, df2 = create_matrix(df, users_col, items_col, ratings_col, threshold)
X

item_id
user_id
rating


<ipython-input-5-f15f021da9c0>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[ratings_col] = 1
<ipython-input-5-f15f021da9c0>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[col] = data[col].astype('category')


<6039x3628 sparse matrix of type '<class 'numpy.longlong'>'
	with 836478 stored elements in Compressed Sparse Row format>

In [7]:
def create_train_test(ratings, test_size = 0.2, seed = 1234):
    assert test_size < 1.0 and test_size > 0.0

    # Dictionary Of Keys based sparse matrix is more efficient
    # for constructing sparse matrices incrementally compared with csr_matrix
    train = ratings.copy().todok()
    test = dok_matrix(train.shape)
    
    # for all the users assign randomly chosen interactions
    # to the test and assign those interactions to zero in the training;
    # when computing the interactions to go into the test set, 
    # remember to round up the numbers (e.g. a user has 4 ratings, if the
    # test_size is 0.2, then 0.8 ratings will go to test, thus we need to
    # round up to ensure the test set gets at least 1 rating)
    rstate = np.random.RandomState(seed)
    for u in range(ratings.shape[0]):
        split_index = ratings[u].indices
        n_splits = ceil(test_size * split_index.shape[0])
        test_index = rstate.choice(split_index, size = n_splits, replace = False)
        test[u, test_index] = ratings[u, test_index]
        train[u, test_index] = 0
    
    train, test = train.tocsr(), test.tocsr()
    return train, test

In [8]:
X_train, X_test = create_train_test(X, test_size = 0.2, seed = 1234)
print(X_train.shape)
print(X_test.shape)

(6039, 3628)
(6039, 3628)


In [9]:
class BPR:
    """
    Bayesian Personalized Ranking (BPR) for implicit feedback data

    Parameters
    ----------
    learning_rate : float, default 0.01
        learning rate for gradient descent

    n_factors : int, default 20
        Number/dimension of user and item latent factors

    n_iters : int, default 15
        Number of iterations to train the algorithm
        
    batch_size : int, default 1000
        batch size for batch gradient descent, the original paper
        uses stochastic gradient descent (i.e., batch size of 1),
        but this can make the training unstable (very sensitive to
        learning rate)

    reg : int, default 0.01
        Regularization term for the user and item latent factors

    seed : int, default 1234
        Seed for the randomly initialized user, item latent factors

    verbose : bool, default True
        Whether to print progress bar while training

    Attributes
    ----------
    user_factors : 2d ndarray, shape [n_users, n_factors]
        User latent factors learnt

    item_factors : 2d ndarray, shape [n_items, n_factors]
        Item latent factors learnt

    References
    ----------
    S. Rendle, C. Freudenthaler, Z. Gantner, L. Schmidt-Thieme 
    Bayesian Personalized Ranking from Implicit Feedback
    - https://arxiv.org/abs/1205.2618
    """
    def __init__(self, learning_rate = 0.01, n_factors = 15, n_iters = 10, 
                 batch_size = 1000, reg = 0.01, seed = 1234, verbose = True):
        self.reg = reg
        self.seed = seed
        self.verbose = verbose
        self.n_iters = n_iters
        self.n_factors = n_factors
        self.batch_size = batch_size
        self.learning_rate = learning_rate
        
        # to avoid re-computation at predict
        self._prediction = None
        
    def fit(self, ratings):
        """
        Parameters
        ----------
        ratings : scipy sparse csr_matrix, shape [n_users, n_items]
            sparse matrix of user-item interactions
        """
        indptr = ratings.indptr
        indices = ratings.indices
        n_users, n_items = ratings.shape
        
        # ensure batch size makes sense, since the algorithm involves
        # for each step randomly sample a user, thus the batch size
        # should be smaller than the total number of users or else
        # we would be sampling the user with replacement
        batch_size = self.batch_size
        if n_users < batch_size:
            batch_size = n_users
            sys.stderr.write('WARNING: Batch size is greater than number of users,'
                             'switching to a batch size of {}\n'.format(n_users))

        batch_iters = n_users // batch_size
        
        # initialize random weights
        rstate = np.random.RandomState(self.seed)
        self.user_factors = rstate.normal(size = (n_users, self.n_factors))
        self.item_factors = rstate.normal(size = (n_items, self.n_factors))
        
        # progress bar for training iteration if verbose is turned on
        loop = range(self.n_iters)
        if self.verbose:
            loop = trange(self.n_iters, desc = self.__class__.__name__)
        
        for _ in loop:
            for _ in range(batch_iters):
                sampled = self._sample(n_users, n_items, indices, indptr)
                sampled_users, sampled_pos_items, sampled_neg_items = sampled
                self._update(sampled_users, sampled_pos_items, sampled_neg_items)

        return self
    
    def _sample(self, n_users, n_items, indices, indptr):
        """sample batches of random triplets u, i, j"""
        sampled_pos_items = np.zeros(self.batch_size, dtype = np.int)
        sampled_neg_items = np.zeros(self.batch_size, dtype = np.int)
        sampled_users = np.random.choice(
            n_users, size = self.batch_size, replace = False)
       
        for idx, user in enumerate(sampled_users):
            pos_items = indices[indptr[user]:indptr[user + 1]]
            
            if(len(pos_items)>0):
                pos_item = np.random.choice(pos_items)
                sampled_pos_items[idx] = pos_item
            neg_item = np.random.choice(n_items)
            while neg_item in pos_items:
                neg_item = np.random.choice(n_items)

            
            sampled_neg_items[idx] = neg_item

        return sampled_users, sampled_pos_items, sampled_neg_items
                
    def _update(self, u, i, j):
        """
        update according to the bootstrapped user u, 
        positive item i and negative item j
        """
        user_u = self.user_factors[u]
        item_i = self.item_factors[i]
        item_j = self.item_factors[j]
        
        # decompose the estimator, compute the difference between
        # the score of the positive items and negative items; a
        # naive implementation might look like the following:
        # r_ui = np.diag(user_u.dot(item_i.T))
        # r_uj = np.diag(user_u.dot(item_j.T))
        # r_uij = r_ui - r_uj
        
        # however, we can do better, so
        # for batch dot product, instead of doing the dot product
        # then only extract the diagonal element (which is the value
        # of that current batch), we perform a hadamard product, 
        # i.e. matrix element-wise product then do a sum along the column will
        # be more efficient since it's less operations
        # http://people.revoledu.com/kardi/tutorial/LinearAlgebra/HadamardProduct.html
        # r_ui = np.sum(user_u * item_i, axis = 1)
        #
        # then we can achieve another speedup by doing the difference
        # on the positive and negative item up front instead of computing
        # r_ui and r_uj separately, these two idea will speed up the operations
        # from 1:14 down to 0.36
        r_uij = np.sum(user_u * (item_i - item_j), axis = 1)
        sigmoid = np.exp(-r_uij) / (1.0 + np.exp(-r_uij))
        
        # repeat the 1 dimension sigmoid n_factors times so
        # the dimension will match when doing the update
        sigmoid_tiled = np.tile(sigmoid, (self.n_factors, 1)).T

        # update using gradient descent
        grad_u = sigmoid_tiled * (item_j - item_i) + self.reg * user_u
        grad_i = sigmoid_tiled * -user_u + self.reg * item_i
        grad_j = sigmoid_tiled * user_u + self.reg * item_j
        self.user_factors[u] -= self.learning_rate * grad_u
        self.item_factors[i] -= self.learning_rate * grad_i
        self.item_factors[j] -= self.learning_rate * grad_j
        return self

    def predict(self):
        """
        Obtain the predicted ratings for every users and items
        by doing a dot product of the learnt user and item vectors.
        The result will be cached to avoid re-computing it every time
        we call predict, thus there will only be an overhead the first
        time we call it. Note, ideally you probably don't need to compute
        this as it returns a dense matrix and may take up huge amounts of
        memory for large datasets
        """
        if self._prediction is None:
            self._prediction = self.user_factors.dot(self.item_factors.T)

        return self._prediction

    def _predict_user(self, user):
        """
        returns the predicted ratings for the specified user,
        this is mainly used in computing evaluation metric
        """
        user_pred = self.user_factors[user].dot(self.item_factors.T)
        return user_pred

    def recommend(self, ratings, N = 5):
        """
        Returns the top N ranked items for given user id,
        excluding the ones that the user already liked
        
        Parameters
        ----------
        ratings : scipy sparse csr_matrix, shape [n_users, n_items]
            sparse matrix of user-item interactions 
        
        N : int, default 5
            top-N similar items' N
        
        Returns
        -------
        recommendation : 2d ndarray, shape [number of users, N]
            each row is the top-N ranked item for each query user
        """
        n_users = ratings.shape[0]
        recommendation = np.zeros((n_users, N), dtype = np.uint32)
        for user in range(n_users):
            top_n = self._recommend_user(ratings, user, N)
            recommendation[user] = top_n

        return recommendation

    def _recommend_user(self, ratings, user, N):
        """the top-N ranked items for a given user"""
        scores = self._predict_user(user)
        print("scores")
        print(scores)
        # compute the top N items, removing the items that the user already liked
        # from the result and ensure that we don't get out of bounds error when 
        # we ask for more recommendations than that are available
        liked = set(ratings[user].indices)
        count = N + len(liked)
        if count < scores.shape[0]:

            # when trying to obtain the top-N indices from the score,
            # using argpartition to retrieve the top-N indices in 
            # unsorted order and then sort them will be faster than doing
            # straight up argort on the entire score
            # http://stackoverflow.com/questions/42184499/cannot-understand-numpy-argpartition-output
            ids = np.argpartition(scores, -count)[-count:]
            best_ids = np.argsort(scores[ids])[::-1]
            best = ids[best_ids]
        else:
            best = np.argsort(scores)[::-1]

        top_n = list(islice((rec for rec in best if rec not in liked), N))
        return top_n
    
    def get_similar_items(self, N = 5, item_ids = None):
        """
        return the top N similar items for itemid, where
        cosine distance is used as the distance metric
        
        Parameters
        ----------
        N : int, default 5
            top-N similar items' N
            
        item_ids : 1d iterator, e.g. list or numpy array, default None
            the item ids that we wish to find the similar items
            of, the default None will compute the similar items
            for all the items
        
        Returns
        -------
        similar_items : 2d ndarray, shape [number of query item_ids, N]
            each row is the top-N most similar item id for each
            query item id
        """
        # cosine distance is proportional to normalized euclidean distance,
        # thus we normalize the item vectors and use euclidean metric so
        # we can use the more efficient kd-tree for nearest neighbor search;
        # also the item will always to nearest to itself, so we add 1 to 
        # get an additional nearest item and remove itself at the end
        normed_factors = normalize(self.item_factors)
        knn = NearestNeighbors(n_neighbors = N + 1, metric = 'euclidean')
        knn.fit(normed_factors)

        # returns a distance, index tuple,
        # we don't actually need the distance
        if item_ids is not None:
            normed_factors = normed_factors[item_ids]

        _, items = knn.kneighbors(normed_factors)
        similar_items = items[:, 1:].astype(np.uint32)
        return similar_items

In [10]:

bpr_params = {'reg': 0.01,
              'learning_rate': 0.1,
              'n_iters': 160,
              'n_factors': 15,
              'batch_size': 100}

bpr = BPR(**bpr_params)
bpr.fit(X_train)

BPR: 100%|██████████| 160/160 [00:36<00:00,  4.39it/s]


In [11]:
def auc_score(model, ratings):
    """
    computes area under the ROC curve (AUC).
    The full name should probably be mean
    auc score as it is computing the auc
    for every user's prediction and actual
    interaction and taking the average for
    all users
    
    Parameters
    ----------
    model : BPR instance
        Trained BPR model
        
    ratings : scipy sparse csr_matrix, shape [n_users, n_items]
        sparse matrix of user-item interactions
    
    Returns
    -------
    auc : float 0.0 ~ 1.0
    """
    auc = 0.0
    n_users, n_items = ratings.shape
    for user, row in enumerate(ratings):
        y_pred = model._predict_user(user)
        
        y_true = np.zeros(n_items)
        print(y_pred)
        y_true[row.indices] = 1
        if(np.unique(y_true).size>1):
            auc += roc_auc_score(y_true, y_pred)

    auc /= n_users
    return auc

In [12]:
print(auc_score(bpr, X_train))
print(auc_score(bpr, X_test))

[ 3.8609598   1.60035135  0.51271771 ... -2.18755854 -0.55048607
  2.0453088 ]
[ 3.67811411  1.25305292 -0.72129477 ... -2.17486214 -1.51888235
  0.46051685]
[ 3.75411766  1.66191163  1.27025505 ... -0.20025153 -1.1459582
  1.95931344]
[ 3.29379149  2.09263893 -0.46013018 ... -3.65538591 -2.33317367
  0.4530817 ]
[2.84620995 1.2831295  2.31195858 ... 0.87100387 0.38994997 1.84796124]
[ 2.23628848  2.14795405  0.26305528 ... -2.25484489 -0.58123196
  0.43336001]
[ 4.06806446  2.54168219  1.31426931 ... -1.82256363 -0.82072805
  1.67982391]
[ 4.09346656  2.02098106 -0.39537811 ... -2.95169105 -1.72483625
  0.53700062]
[ 4.84565421  2.51895576 -0.07327032 ... -2.26316101 -1.76335691
  1.1410702 ]
[ 2.54985629  2.2655471   0.97125114 ... -0.67024134 -0.16237108
  1.18620301]
[ 3.5309405   2.05815147  1.6525564  ... -0.8992395  -0.90871509
  1.6080939 ]
[ 2.50367941  0.88960529 -0.26279827 ... -1.8352082  -1.53652568
  1.32587481]
[ 3.22777585  2.32049253  0.00772497 ... -3.15269239 -1.8445

[ 2.95904727  1.47800992  0.38422774 ... -0.54357674 -0.76768505
  0.61435425]
[ 5.10029186  1.66705378  0.09404044 ... -2.58170009 -1.83018734
  0.99910884]
[ 3.39446729  1.84897507  0.2204671  ... -1.9259736  -1.7975995
 -0.2268416 ]
[ 4.50113187  2.41327901  1.72346734 ... -0.39158675 -0.25344482
  2.93926595]
[ 4.26809188  1.9830369  -0.26341685 ... -2.85190606 -1.87277076
  0.01779815]
[ 3.73888304  1.58348489 -0.66586735 ... -2.09064452 -0.5818977
  1.57967309]
[ 3.44774585  1.20246791  1.43125798 ... -0.014479   -1.03669442
  3.16492048]
[ 3.93629303  1.80789019 -0.36427553 ... -2.30934569 -0.73019619
  0.13419303]
[ 3.64023064  1.30191743  0.28260688 ... -0.75107367 -1.57799826
  1.45816071]
[ 1.66125358  2.11421087  1.42129077 ... -1.0582463  -0.20901878
 -0.11000547]
[ 2.7277741   2.20071737  0.32616578 ... -2.08035594 -1.04217401
 -1.36046056]
[ 4.44463472  2.40761154  0.37574266 ... -1.32512424 -1.91494227
  1.18514748]
[ 3.35476576  2.02691933  0.66800629 ... -1.34684359 -

[ 2.78600607  2.49998659  2.46431327 ... -0.62698242 -0.18727224
  2.13338515]
[ 3.79623885  2.67393144  1.47363611 ... -1.24981496 -1.29424064
  1.51046563]
[ 3.73105231  1.12159781 -0.00768697 ...  0.04597309 -0.74963421
  1.85022495]
[ 2.73762936  0.62801046  0.83632451 ...  1.3513425  -0.10060226
  2.50432538]
[ 4.72063533  2.16371322  0.283655   ... -0.56103921 -1.59808824
  2.22853688]
[ 2.844986    2.03122416  0.7754842  ... -1.49020754 -1.12182014
  0.60268843]
[ 4.50207851  0.88537721  1.31840474 ...  0.56006651 -0.95049097
  1.89555429]
[ 3.25504487  1.03102868 -0.02875042 ... -1.79694398 -0.42987391
  2.52149296]
[ 3.87831585  2.71462978  1.99741401 ... -2.07782263  0.75858713
  0.13253634]
[ 4.85480411  2.00281641  1.18836778 ... -0.67758742 -1.05057468
  2.68714655]
[ 3.7923733   2.84816818  0.64763851 ... -0.95669594 -0.03010579
  4.17443123]
[ 2.05504438  1.11996633  1.05759249 ... -0.46122498 -0.16525225
  1.05105528]
[ 3.38066663  1.40066102  0.88463308 ... -0.96904502

[ 2.8849504   2.56195929  1.15067058 ... -0.9034681   0.74619024
  4.04893771]
[ 2.34970952  1.04369431 -0.32602995 ... -1.03755361 -0.63412288
  0.70933972]
[ 3.41449975  1.2899305   0.06236554 ... -0.12261245 -1.11356276
  2.12963361]
[ 3.89086242  2.09871623  0.59146891 ... -2.10819575 -2.07501831
 -0.77296916]
[ 4.1815532   2.12003602  0.67027293 ... -1.70250467 -1.68112342
  1.18187874]
[ 2.76071677  1.51413783  0.40628629 ... -1.42978061 -1.48626951
  0.8530974 ]
[ 4.02253797  2.6222057   1.49047021 ... -1.92788822 -1.286221
  1.45257826]
[ 2.84715541  0.45400163  0.70505372 ... -0.49064436  0.08402206
  1.3318922 ]
[ 4.84967716  1.93992144 -0.75559129 ... -3.07669315 -2.70322746
 -1.06502788]
[ 4.6527017   2.66341706 -0.65694777 ... -3.08696488 -1.40994756
  1.6716622 ]
[ 4.232318    1.16420016  0.48784606 ... -0.26044023 -1.35852363
  1.37453475]
[ 2.49437542  1.59094679  0.25736564 ... -2.36760502 -0.73433364
 -0.78730877]
[ 3.60413106  1.51277345  0.15976703 ... -1.35556644 -

[ 4.41226977  2.37827146 -0.33903561 ... -3.75800713 -1.85167906
 -0.52875922]
[ 3.43488086  1.71139286  0.14024926 ... -0.86909494 -0.30800491
  2.44244465]
[ 3.43316315  1.52710728 -0.00523205 ... -1.70123042 -1.23246344
  2.18859561]
[ 2.13424921  2.0340835   1.52681261 ... -0.3216453  -0.09800395
  0.35588774]
[ 3.19961999  1.55048977  0.9968157  ... -0.41981903 -0.94326573
  0.05250024]
[ 5.42087891  1.89923658  1.57360123 ... -1.40258627 -2.17149273
  2.41475814]
[ 4.05149708  2.11988775 -1.16167617 ... -3.26921835 -1.23225079
  0.90566251]
[ 2.7229326   1.64106902 -0.14309404 ... -1.4912551  -1.12861156
  0.37529368]
[ 3.88297172  1.8388342   1.6796243  ... -0.20775225 -1.12204792
  1.4874419 ]
[ 4.53036395  0.98598733  0.51809584 ... -0.60658656 -0.34537346
  0.65445482]
[ 4.33090701  3.08789783 -0.27736002 ... -3.48800464 -2.0106704
  0.0930521 ]
[ 4.3412638   1.2778768   0.99267421 ...  0.52529268 -1.9726055
  2.48210438]
[ 5.76263337  2.50471238  1.25662079 ... -1.21578824 -

...

[ 3.23783977  2.4669412  -2.03190902 ... -5.12491768 -2.28688635
  0.21936503]
[3.78826632 1.51203918 1.50400012 ... 0.26054043 0.05258836 0.89868292]
[ 4.49535642  2.44912298  0.86988764 ... -2.0878052  -0.37689602
  0.38895321]
[ 4.39955043  2.52033482  1.42282457 ... -0.15266584  0.5565777
  1.77048508]
[ 4.15284225  1.36252548  1.36836096 ... -0.29901777 -1.17198658
  1.84273128]
[ 3.81382358  2.62424127  1.47393371 ... -1.35701093  0.0125767
  1.22046103]
[ 4.2133107   0.89152818 -1.80295385 ... -3.76345413 -2.47457214
 -0.28866332]
[ 3.10569499  1.34745637  0.83640378 ... -1.39648312 -1.04802751
  0.85208073]
[ 3.19617758  1.71706375  0.28919176 ... -1.78893977 -1.90274142
  0.84083194]
[ 4.14869612  1.77896443  0.26198627 ... -2.83039335 -1.22687246
 -0.20735745]
[ 2.59328668  1.4143466   0.71828048 ... -1.86374292 -1.04294657
  0.6909893 ]
[ 2.55911617  1.3859694   0.26119908 ... -0.71733693 -0.56369545
  1.94844112]
[ 3.50511962  2.14314022  0.92038007 ... -2.40830941 -1.75020

[ 3.4869877   1.44025616 -0.11438882 ... -2.29505168 -0.91517785
 -0.02456325]
[ 4.51297536  2.61651251 -1.504177   ... -4.98054938 -2.6085921
 -1.28667499]
[ 2.92870457  1.4006649  -0.17487211 ... -1.61697266 -0.66532259
  0.68829469]
[ 4.5505456   1.92834979  1.6381072  ... -0.39504312 -1.36771712
  1.08690147]
[ 2.90310832  1.02507433 -0.55206967 ... -1.42289491 -1.97364352
  1.41796515]
[ 2.32586447  1.53987683  0.01952637 ... -1.19269148 -1.06786443
  1.1397092 ]
[ 4.40074597  2.99351645 -1.05227872 ... -3.1362185  -1.59005639
 -0.17503902]
[ 2.36951949  1.17357628  1.13457142 ... -0.29346065 -0.30212771
  1.1895855 ]
[ 4.8759715   1.65275137  1.0336504  ... -0.73680581 -1.60891538
  2.21612785]
[ 4.36174404  2.67640099  0.1621269  ... -1.95479233 -2.09376254
  1.34839772]
[ 3.93612281  2.65535119  0.30034649 ... -2.06249714 -1.32239837
  1.27917309]
[ 2.31708113  1.27691883  0.89648088 ... -0.88922346 -0.23946911
  0.36460304]
[ 4.32704643  2.39166811 -0.20064257 ... -2.19602292 

[ 4.19016403  2.00453452  0.16843381 ... -3.28675419 -2.08969646
  0.22724862]
[ 4.4646239   2.14269772 -0.20817703 ... -3.4134135  -2.82011452
  0.11441251]
[ 3.24380713  1.46499609  0.79317582 ... -0.14965689 -0.20646756
  1.22872857]
[ 0.97071195  1.79271529 -0.12308506 ... -1.24571784 -0.28943336
  0.39058029]
[ 3.42440067  2.4180899  -0.02642402 ... -2.52317963 -1.50909789
  0.72900413]
[ 3.45330656  1.20408208  0.41745735 ... -1.25652876  0.01959141
 -1.0490198 ]
[ 2.51499787  1.12945736 -0.28204548 ... -0.60650011 -0.20829954
  1.47067391]
[ 5.10417113  3.09315432  1.53991458 ... -2.33244817 -0.71952269
  1.52287041]
[ 4.71924353  2.03836018 -0.29040368 ... -2.61079491 -1.67498659
  0.81386675]
[3.60383985 1.85154337 3.14251038 ... 0.60626719 0.45699163 2.44301877]
[ 3.65238248  1.21715292 -0.74179059 ... -2.07853462 -1.31306579
  0.91285619]
[ 3.43379523  2.79414398  2.24259758 ... -1.12849707  0.03949691
  1.02199511]
[ 3.57336274  1.78653144  1.24052629 ... -0.54061556  0.018

[ 3.01357001  1.40116719  0.01905928 ... -2.76673029 -1.44197661
 -0.10534974]
[ 3.47141107  2.18923002  0.56809062 ... -1.5224005  -1.54428441
  0.87901878]
[ 4.97721417  2.11904321 -0.43036972 ... -2.38687361 -1.3907188
  0.34285161]
[ 2.09747283  1.04190655  0.99489055 ...  0.22718093 -0.84305039
  1.97213512]
[ 2.21215531  1.61693434 -0.29476153 ... -1.77326741 -1.11956625
  0.13762027]
[ 3.2357595   2.66188499  1.0098527  ... -3.04276625 -1.38727815
  1.16082475]
[ 3.88930912  1.88461603  1.22834853 ... -2.10397032 -2.17414554
  2.3290665 ]
[ 3.64462165  2.02850754  0.474216   ... -2.26911822 -1.6635403
  0.4683154 ]
[ 3.73378178  1.62438068 -0.63457214 ... -1.85797425 -1.10158856
  1.5011618 ]
[ 3.86819624  2.25360705  0.94607899 ... -1.24595539 -0.89684379
  0.98311949]
[ 3.84982369  2.10312059  0.0273883  ... -1.57545779 -0.70012096
  0.98060856]
[ 3.86925804  2.16057134  0.30165704 ... -1.95746405 -1.92888884
  1.71641499]
[ 4.87850676  3.16992268  1.55947734 ... -2.71515945 -

[ 3.57934349  1.29175402 -0.27494589 ... -2.52711964 -0.88320959
  0.87481054]
[ 4.03194345  1.59209282 -0.13229903 ... -1.81067502 -0.9343005
  2.75113857]
[ 3.21874234  1.49759098 -0.27088488 ... -2.01120665 -0.26116487
  0.73181428]
[ 4.07361359  2.45674506  2.85372146 ... -1.22945147  1.67016651
  2.65234723]
[ 3.90340683  2.38789384 -0.0481501  ... -3.28690391 -1.96455397
 -0.12011869]
[ 3.30975174  1.77802938  1.81763038 ... -0.40365838  0.50128524
  1.43228057]
[ 3.34156056  1.65112777 -0.29624526 ... -2.02997926 -1.13899842
 -0.4928871 ]
[ 2.78610412  1.60751606  0.34219376 ... -1.05343368 -0.94156361
  1.00913178]
[ 5.19157493  2.20896134  0.28943205 ... -2.75772823 -1.49032571
  1.53116494]
[ 3.33324217  2.10225354 -0.10473388 ... -1.45129644 -1.68885098
  0.06447418]
[ 3.9916437   3.14618273  1.03501817 ... -2.7111806  -0.76456871
 -0.27819624]
[ 1.94994989  2.16542814  2.11871198 ... -1.40021915 -1.12781202
 -0.05076701]
[ 4.0743216   0.43319401  0.47617309 ... -1.18519712 

In [13]:
bpr.get_similar_items(N = 5)

array([[2845, 1355, 2155, 1081,  342],
       [ 687,  456, 1246,  353,  568],
       [3153, 1693, 2784, 2464, 2643],
       ...,
       [2374,  296, 3105, 1357, 1310],
       [3545, 2176, 3028,  246, 1036],
       [3570, 3026, 3541, 3012, 2912]], dtype=uint32)

In [14]:
bpr.recommend(X_train, N = 5)

scores
[ 3.8609598   1.60035135  0.51271771 ... -2.18755854 -0.55048607
  2.0453088 ]
best
[2549 1003  342 1152  573 3110  249 1116    0 1113 1132 2462 2813 2507
 1141 1861 1858 3356 1540 1140  838 2886  949 1007 1541  618 1689 1419
 2445 2804 2657 1104 1081  843 1189 1233 2377 2724 3304 1810  363  569
 1377 2734 1058 1080 1147]
scores
[ 3.67811411  1.25305292 -0.72129477 ... -2.17486214 -1.51888235
  0.46051685]
best
[2600  249   49    0  587 1080 1152 1003 1088 2902 2507 1098 3122 2155
 2462  573 2325  569 1109 1865 1081  509  842 3433 1455   33 1035  821
 1078 2549  283 3110 3125 2734  342 3435 1267 2154  831 1105 2165 2062
   24 1131 1167 1147 1113 1233 2051  888  106 1082  941 2845 2542 3356
 1126 1419 2351 1090 1810 1160 1132 1094 1532 3270 1026 2084  213  618
 1186 1802  990  568  985 2284 3306 1149 1189  838  462  852  785  818
 1355  153 3586 2772 3067  305 1129  698 1473  843 3303  872 1158]
scores
[ 3.75411766  1.66191163  1.27025505 ... -0.20025153 -1.1459582
  1.95931344]


 1140  570 2389  135 2832  791 2474 3304 3383  859]
scores
[ 4.09033436  3.27578949  1.06893433 ... -2.23672567 -0.90352049
  0.81661735]
best
[1003  249 1141 2600  785 2549 1455 1080 2462 1026 1189  569 1081 1152
  843   33 1098  305 2377 1260  573 1895 1419]
scores
[ 3.4791269   2.04361745  1.46002479 ... -0.39203979  0.12176272
  2.14677408]
best
[ 249 2600 1141 2462  569  573 3180 2549 3270  843 3110 2377 1084 1080
   33  342 3435 1132 1540 1152  785  106 1026  509 2902 1260 1003 3574
 2734 1094 2445 2064 1078  618 3356  842 1810  949 1113 2214 1455 1743
 2154  587  888 2155 1149 1391  983  462 2325 1081 1098  832 1134  698
 3387  941 2062 1419 1747]
scores
[ 3.6278759   0.76400653  0.92520935 ... -0.97915607  0.1922289
  0.17177056]
best
[  16 1189 1540 2051  573 2155 2734 1035 3170 1858    0  283 1096 3356
 2549  785 3110  587 1118  342 2062   33  830   49 2804 2792 1077 2799
 2351  224 1134 1802 1147 3122  343 2462  249]
scores
[ 1.98714887  1.52526596 -0.0952317  ... -1.1601948

best
[3209 2600 2889 3210 3122  392 1131 3270 1495 3490 2431 2154  255 3434
 2297 3312  342 3231  590  213 2095]
scores
[ 4.72063533  2.16371322  0.283655   ... -0.56103921 -1.59808824
  2.22853688]
best
[2600  249 2549 1131 1098    0 1080  569 1141 2154 1455 2902 1081 1109
 1026 1003 3270 2155 3110 1419 1105  106 3180  342 3122 1782  462  568
 2462   33 1113  587  283 2542 2053 1810 1266 2445 3433  315 1152 3428
  948 2446 2657 1805 2351 1233 2507 3435 2734 1078  573  637 1391 1132
 3546  213 3207 2325 3312 1415  843  255 1505]
scores
[ 2.844986    2.03122416  0.7754842  ... -1.49020754 -1.12182014
  0.60268843]
best
[ 521 2600 1081 1415 2657 2453 2515 1419 2508 1691  618 2813 2326 2435
 1700 2366  727  303  684 3434 2187   38 2431 1251  213 2902 2445 1659
  722 2452 2470 2970 1584 2998 2886  283  249 1446 2462 2441  366 2785
 2507 3311   20 2155 3437 1365 2732 2325 3586 3183 2456 2112 3110 3187
 2377    0 2623  156 2971 1750 1560   10 2968 3224  350 2114 1579  424
  363 1098 1369 124

best
[2462  249 1189 2600 1147 1419  521 1003 2431 1081  618   33  785 2507
  342 2155 2657 2114  283 1455 1540 2724 1080 2902  569  305    0 1094
 1097   49  439  573 2515   16]
scores
[ 3.33568571  1.45093557 -0.86746107 ... -2.0520063  -1.15268076
  1.30067734]
best
[ 842 1113 2600 2549 2154 3122 1078 1080  587 1455   33  249 1109   49
    0 1131 1149 1267  831 2051 1003 1105 2062 2155  342  573 1145 1126
  785 1810 1233 3125 1041 1727 2734 2462 3356  843 1092 2351 1152  888
 3549 1189 1088 1071 1132 3166  509 1160 1865  985  828 3574 2804 1058
 1186  852]
scores
[ 4.61701566  2.48250741  0.3816308  ... -2.1822627  -1.15163355
  1.15375693]
best
[ 249 2600 1080 2462 3110 1141 2902  569 1152 1003 1081 2549 1078    0
  843  509 1455 1109  573 1098  785 3180  342 1113 1084  106 1810 3270
 1026   49  698  983 1149 2377 1743 2734 2062 1105  888 1260  842]
scores
[ 4.68901376  2.18923352  0.99506754 ... -3.63937902 -2.0257727
 -0.48067497]
best
[1081    0 2902  618 1152 1736 1173 1122 126

best
[ 249 2600  569 2462 1080 1260 1084 1098 2285  785 1750  509 2325   49
  283 1152 2902 1455 1081  523 2657  305 2377  462 1082 1189 1094 1003
 1147 1419  949  618 1105 1141  439    0  587   33 3224 1248  722 2542
  843 2155   16  573 3387 3110  888 1097 1149 1000 1810 2507 1173 1415
 1160  831   31 1246 2685 3270 1540 3339 1783 1078 2064 2722 3180  106
 3248  698  572 3119  342 2389 1940 1584 1782 1122  996 1106 1743 2549
 1035 2283 1895 1026 1083 2452  684  995  280 2734 3388 1109 1736 1278
 1176 2084 2697  838 1355  423 1103 1233  363 2536 2089  456 2445 2214
 1834 1485 2446 2971 1186 3574 2877 2165 3437 3423 3170 1735 3435 1028
 1691 1104 1267 2298 1144  213  827 3239 2439 1462 1973 1145 1423 2406
 1448 2724 3383 3122  568 1231 1277   35 2114 1116 1090  983 2659 1131
 1132 1250  567 1954 3175 3433 1244  985 2785   20 1779   46 2081 1092
 1885 1167  687 2125 1154 2656  353 3386 1505 2689  941 3474 2794 1158
 1659 1532  366 1001 1124 2802 3385 1065 1099 3196 2970 3307 2613 1803
 

...

  1.3832336 ]
best
[ 249    0 2462  342 2600  569 3110  618  573 1152 2507 1419 1080 1003
   49 1189 1081 2155 2549 1094 2445  106 2734  283 1540]
scores
[ 4.26853385  2.00643247 -2.68911669 ... -3.78426218 -1.93365433
  0.62985055]
best
[1105  587  831  842   49 3125  249 1267 1149 1802 1058 1080 1727 2542
 3067 1455 1112 1109 1189 3136 2549 2600 1129 1083 1134 1152 1158 1131
  283 2325 1035 2772  823  509 1090 1473  859 1092  573 1121    0 1167
 1126 3122 1078 3303  941  153 1130  224 2826  888 1098 3248 1694   16
 2051   33  785 1170 1003  990 1001 1132 1082  569 1106  107  847 1800
  838  828  821   35 2462 1147 1081 2062 1088  822 1233  523 1160  852
  832 1165 1094 1750 3370 1084 3065 2507 1743 1146 1865 1181  996 1000
 1966 1176 1801 3066 1734  817 2685 3356  305 2474 2165 2792 2284 2754
 2084  698 1031 1113 1070 1219 1260 3387  818  841 2155 1144 3054  985
 1116 1154  845 3223 1145  720 2446 1717 2734 1103 1002 3549   24 1810
 2881 3339 2803 1097  932 1355  236  839 2845  994 3

best
[ 843 1083   49  249  573 1152 1098 2285  509 2600  106 1113 1097 3574
 2462 1116  569 1173 1455 2325 1109 2734 1084 2724 1810 1783 1260  990
 2814 1248 2549 2877 1080 1186 3435 3180 2903 1082 2657 1122 1090 1104
 2064 1233 1081 2653  305  842  363 2902 1132 1141 1003   31 3110 2155
 1088 2439 3119  462 1160 1105  342 2507  831 1035 3387 2377  698  439
 2125 1134 2613 1103  587 2084   33    0 1856  888 1750 1078 1094  949
 1085  722 2685 1149 1779 1092  283 1419  986  839 1727 3270 1895 1532
 2697  838 2458  818 1126 1000 3170 3368  823 1145  785 1041 1154 1106
 1183 1743  153 1170 1423  684 2431 1136 1197 1140 1269 3474  720  350
 1861 1736  235 1940  693 1794 2813  827 2742  618 2351  995 2258 1448
 2114 2785 1144 1147 2389 3356 2283 1776 2536  996  523  852  832 1792
 3570 1278  983 3026 1129 2154 1026    9  107 1793 1540 1250 2650 1805
 2089 1888]
scores
[ 2.99324793  2.55370839  0.90274426 ... -2.45045369 -0.49064624
  1.20365714]
best
[1399 3183 3435 1415 2377 3210 2600  249

best
[ 342 2155    0 2600 3110  573   33 1041 2437  941 1113 2549 2114 2377
 1141  213 1189 2878 3122]
scores
[ 3.81300868  0.60634198  0.48405988 ... -1.27352239  0.09276619
  0.92555397]
best
[1116 1189  573 1152 1035 1802    0   49 2155 2084 2051 1181 1858  439
  342 1448  249  832  843 1473 1132  141 2549 1003 3356 2903  509  283
 2734   33 3170 1114  941  785  569  990 3239 1147 2462 1149 1233 2659
 2831 1094 1080 1540  587  618 3041 1727 1140 3125  823   16 1078 1260
 2507 1113 1082 1455  839  888 1084  224 2724  106 1810  949  831   56
 2433  987 1134  852  872 1160 1000 1103 2118 1144 2062 2650  827  833
  954 2886 1081 1091 1532 1182 1278 1041  994  570  821 1925  305]
scores
[ 3.93960108  2.88035861 -0.97657495 ... -2.96776821 -1.51886812
  2.45681264]
best
[1455 2600   49 1473  305 2446 1189   35  283 1097 1560  423 1083 2155
 3574 1081  509 1082 3180  587 1080 1105  249   16 2325 1094  831 1170
  720   38 1092 2439   33  785 1078 1116 2542 2734  764  254 1173 1000
  573 126

best
[ 249 2600 3110 1419 2462 2657 2813 1003 2507  342 1081 2445 2377 1152
  618  462 3435 1098 2549 1415 1147    0 2508 1805 2536 1141  335  684
 2325  569 1080 3224 1094  573   33 1540 1007]
scores
[ 2.74085083  0.5698748   0.88994808 ...  0.30469335 -0.1388827
  2.48934647]
best
[1141 3026 3110 3312 3435  106  249 3270 2600  818 2445  569  342 1104
 1132 3180  823 1462  573 2462 2325  843 2549 2537 3401 1113 3541  941]
scores
[ 4.4380907   2.28546568  1.04507522 ... -0.61448867 -1.24922559
  1.06800154]
best
[2600 2155 2902 2446  283 1081 2515 3270  249 2154    0 2351 2453  213
  106 2734  569 1455 2462 1080 3122 2452 1078 1419 3180 3110 2114 2326
 2431 3434   33  509 1584 1505   38   49 2128 2623  342  785 1795 3231
  305 2697 2445  521 1094 2970   16 1097 1369  587  482 2724 2334 1026
 1098 2657 3574 2968 2456  568 2325 3428 2506 2285 1082 2377 2064 1147
 1810  618 2439 3207  727 3586 2081   20 2053 2542  462 3437 2051 1560
 2889 2845 1782 3433  255]
scores
[ 3.08934559  1.572022

array([[ 342,  573, 3110, 1116, 1113],
       [2600,  249,   49,    0,  587],
       [2155, 2902,  283, 2154, 1078],
       ...,
       [2600,    0, 1080, 2155, 1081],
       [1113,  573, 1141,  342, 2600],
       [2549,  573, 2155, 1003, 1113]], dtype=uint32)

AttributeError: 'BPR' object has no attribute 'recommend_user'